#### **1. Installation & Checks**

In [1]:
#Import required libraries and functions
from sahi import AutoDetectionModel
from sahi.utils.cv import read_image, read_image_as_pil
from sahi.utils.file import Path, increment_path, list_files, save_json, save_pickle, download_from_url
from sahi.predict import get_prediction, get_sliced_prediction, predict, agg_prediction, get_prediction_batched, get_sliced_prediction_batched, predict 
from sahi.prediction import visualize_object_predictions
from sahi.postprocess.utils import ObjectPredictionList, has_match, merge_object_prediction_pair
from IPython.display import Image
from numpy import asarray
from tqdm import tqdm
from PIL import Image
from sahi.prediction import ObjectPrediction, PredictionResult
from pathlib import Path
from multiprocessing import Pool, cpu_count
from torchvision.ops import nms, batched_nms, clip_boxes_to_image
#from ensemble_boxes import weighted_boxes_fusion
from sahi.postprocess.ensemble_boxes_wbf import weighted_boxes_fusion
import cv2
import os
import time
import json
import numpy as np
import time
import torch

#### **2. Object Instantiantion**

******YOLOv8-N******

In [2]:
#create the model instance
baseline_yolo8_model_path = 'models/baseline/yolov8n.pt'
baseline_yolov8_detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov8',
        model_path=baseline_yolo8_model_path,
        confidence_threshold=0.25,
        device="cuda:0", # or 'cpu'
)

In [3]:
#create the model instance
pretrained_yolo8_50_model_path = 'models/yolov8-mixed-50/last.pt'
yolov8__50_detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov8',
        model_path=pretrained_yolo8_50_model_path,
        confidence_threshold=0.25,
        device="cuda:0", # or 'cpu'
)

In [4]:
#create the model instance
pretrained_yolo8_model_path = 'models/fine-tuned/full/YOLOv8n/last.pt'
yolov8_detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov8',
        model_path=pretrained_yolo8_model_path,
        confidence_threshold=0.1,
        device="cuda:0", # or 'cpu'
)

In [6]:
#create the model instance
pretrained_mixed_yolo8_model_path = 'models/fine-tuned/mixed/YOLOv8n/last.pt'
mixed_detection_yolov8_model = AutoDetectionModel.from_pretrained(
        model_type='yolov8',
        model_path=pretrained_mixed_yolo8_model_path,
        confidence_threshold=0.25,
        device="cuda:0", # or 'cpu'
)

******YOLOv11-N******

In [16]:
#create the model instance
pretrained_yolo11_50_model_path = 'models/yolov11-mixed-50/last.pt'
yolov11__50_detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov11',
        model_path=pretrained_yolo11_50_model_path,
        confidence_threshold=0.1,
        device="cuda:0", # or 'cpu'
)

In [6]:
#create the model instance
pretrained_yolo11_model_path = 'models/fine-tuned/full/YOLOv11n/last.pt'
yolov11_detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov11',
        model_path=pretrained_yolo11_model_path,
        confidence_threshold=0.1,
        device="cuda:0", # or 'cpu'
)

In [7]:
#create the model instance
pretrained_mixed_yolo11_model_path = 'models/fine-tuned/mixed/YOLOv11n/last.pt'
mixed_detection_yolov11_model = AutoDetectionModel.from_pretrained(
        model_type='yolov11',
        model_path=pretrained_mixed_yolo11_model_path,
        confidence_threshold=0.1,
        device="cuda:0", # or 'cpu'
)

#### **3. Functions and Requirements Setup**

In [7]:
#Functions to set the overlap ratio and slice size as per detected objects count in each slice
def get_slice_parameters(object_density, slice_size):
    
    if object_density >= 50:
        #slice_size = min_dim // 4
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.5
        overlap_height_ratio = 0.5
    elif 25 <= object_density < 50:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.25
        overlap_height_ratio = 0.25
    elif 10 <= object_density < 25:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.15
        overlap_height_ratio = 0.15
    else:
        return

    return slice_width, slice_height, overlap_width_ratio, overlap_height_ratio

In [9]:
# Apply Non-Maximum Suppression (NMS)
def apply_nms(detections, iou_threshold=0.5):
    boxes, scores, labels = [], [], []
    for det in detections:
        boxes.append(det.bbox.to_xyxy())
        scores.append(det.score.value)
        labels.append(det.category.id)
    boxes = torch.tensor(boxes, dtype=torch.float32)
    scores = torch.tensor(scores, dtype=torch.float32)
    labels = torch.tensor(labels)

    keep_indices = []
    unique_labels = labels.unique()
    for label in unique_labels:
        idxs = (labels == label).nonzero(as_tuple=False).squeeze(1)
        class_boxes = boxes[idxs]
        class_scores = scores[idxs]
        keep = nms(class_boxes, class_scores, iou_threshold)
        keep_indices.extend(idxs[keep].tolist())

    return [detections[i] for i in keep_indices]

In [10]:
#convert final predictions after NMS merge to COCO format
def merged_preds_to_coco(preds, image_id):
    coco_predictions = []
    for pred in preds:
        try:
            coco = pred.to_coco_prediction(image_id=image_id)
            coco_dict = {
                "image_id": coco.image_id,
                "bbox": coco.bbox,
                "score": coco.score,
                "category_id": coco.category_id,
                "segmentation": coco.segmentation,
                "iscrowd": coco.iscrowd,
                "area": coco.area,
            }
            # Optionally include category_name (not used in COCO eval)
            # coco_dict["category_name"] = coco.category_name

            # Only add if bbox is valid (non-empty)
            if coco_dict["bbox"]:
                coco_predictions.append(coco_dict)
        except Exception as e:
            print(f"Failed to convert to COCO dict: {e}")
    return coco_predictions

In [11]:
# Function to get image details by image_id
def get_image_id(coco_data, image_name):
    for image in coco_data["images"]:
        file_name = Path(image['file_name']).stem
        if file_name == image_name:
            return image['id']
    return None

In [12]:
def predict_multilevel_fine_sliced_images(input_folder, dataset_json_path, detection_model, sliced_detection_model, base_slice_size=512):

    print("\n***********************************************")
    print("Adaptive MultiLevel SAHI Prediction")
    print("*************************************************")
    
    name = "exp"
    save_dir = Path(increment_path(Path("sliced_predictions") / name, exist_ok=False))
    os.makedirs(save_dir, exist_ok=True)

    if dataset_json_path:
        with open(dataset_json_path, "r") as file:
            data = json.load(file)
        
    vis_params = {
        "bbox_thickness": 2,
        "text_size": 0.5,
        "text_thickness": 1,
        "hide_labels": False,
        "hide_conf": False,
        "format": "png"
    }

    image_files = [
        f for f in os.listdir(input_folder)
        if f.lower().endswith((".jpg", ".jpeg", ".png"))
    ]

    print(f"\nRunning fine slicing prediction on {len(image_files)} image(s)...")
    total_prediction_time = 0.0
    grand_total_predictions = 0
    all_coco_preds = []

    for filename in image_files:
        image_path = os.path.join(input_folder, filename)
        image_pil = Image.open(image_path).convert("RGB")
        image_np = np.array(image_pil)
        image_h, image_w = image_np.shape[:2]
        filename_wo_ext = Path(filename).stem
        total_prediction_count = 0
        print("*****************************************")
        print("File Name: ", filename_wo_ext)
        print("*****************************************")
        
        img_id = get_image_id(data, filename_wo_ext) if dataset_json_path else None
        all_object_predictions = []

        #Base prediction
        t0 = time.time()
        intial_prediction = get_prediction(image_path, detection_model)
        t_base = (time.time() - t0)
        print(f"Base pred time: {t_base * 1000:.2f} ms")
        total_prediction_time += t_base
        print(f"Total Based pred time: {total_prediction_time * 1000:.2f} ms")
        full_preds = intial_prediction.object_prediction_list
        full_object_density = len(full_preds)
        print("Full Image Object Density:", full_object_density)

        for pred in full_preds:
            all_object_predictions.append(pred)
            
        total_prediction_count += len(all_object_predictions)
    
        # Split image into 2x2 grid
        grid_h, grid_w = image_h // 2, image_w // 2

        for row in range(2):
            for col in range(2):
                x1, y1 = col * grid_w, row * grid_h
                x2, y2 = min(x1 + grid_w, image_w), min(y1 + grid_h, image_h)
                sub_img = image_pil.crop((x1, y1, x2, y2))
                print("Cropped Image Dimension:", x1, y1, x2, y2)

                time_start = time.time()
                base_pred = get_prediction(sub_img, sliced_detection_model)
                time_end = time.time() - time_start
                
                print("Initial Prediction time is: {:.2f} ms".format(time_end * 1000))

                coarse_preds = base_pred.object_prediction_list
                object_density = len(coarse_preds)
                print("Slice Object Density:", object_density)
                
                slice_params = get_slice_parameters(object_density, base_slice_size)
            
                iteration_time = time_end
                
                preds = coarse_preds.copy()
                
                if slice_params:
                    slice_width, slice_height, overlap_w, overlap_h = slice_params
                    print("********* Slice Parameters ***********")
                    print("Slice Width: ", slice_width)
                    print("Slice Height: ", slice_height)
                    print("Overlap Width Ratio: ", overlap_w)
                    print("Overlap Height Ratio: ", overlap_h)

                    time_start_slice = time.time()
                    sliced_pred = get_sliced_prediction(
                        sub_img,
                        sliced_detection_model,
                        slice_height=slice_height,
                        slice_width=slice_width,
                        overlap_height_ratio=overlap_h,
                        overlap_width_ratio=overlap_w,
                        postprocess_type="NMS",
                        postprocess_match_metric="IOU",
                        postprocess_match_threshold=0.3,
                        postprocess_min_area=16,
                        verbose=0
                    )
                    time_end_slice = time.time() - time_start_slice
                    print("Sliced Prediction time is: {:.2f} ms".format(time_end_slice * 1000))
                    
                    iteration_time += time_end_slice
                    fine_preds = sliced_pred.object_prediction_list
                    print("Pre Adaptive Slicing: ", len(preds))
                    preds.extend(fine_preds)
                    print("Post Adaptive Slicing: ", len(preds))
                else:
                    print("Prediction time is: {:.2f} ms".format(time_end * 1000))

                total_prediction_time += iteration_time
                
                #Offset bounding boxes back to original image space
                for pred in preds:
                    pred.bbox.minx += x1
                    pred.bbox.maxx += x1
                    pred.bbox.miny += y1
                    pred.bbox.maxy += y1
                    all_object_predictions.append(pred)
        
                total_prediction_count += len(preds)

        print("________________________________________________")

        print("Total Prediction Count (Crop+Slice): ", len(all_object_predictions))
        
        # Merge all predictions for image
        merged_preds = apply_nms(all_object_predictions, iou_threshold=0.5)
        
        #object_prediction_list = ObjectPredictionList(all_object_predictions)
        #merged_keep = truncated_nms_merge(object_prediction_list.totensor())
        #selected_object_predictions = object_prediction_list[merged_keep].tolist()
        #if not isinstance(selected_object_predictions, list):
        #    selected_object_predictions = [selected_object_predictions]
        
        # Convert merged predictions to COCO format
        if dataset_json_path:
            coco_preds = merged_preds_to_coco(merged_preds, img_id)
            all_coco_preds.extend(coco_preds)
            
        # Visualization
        visualize_object_predictions(
            image=np.ascontiguousarray(image_pil),
            object_prediction_list=merged_preds,
            rect_th=vis_params["bbox_thickness"],
            text_size=vis_params["text_size"],
            text_th=vis_params["text_thickness"],
            hide_labels=vis_params["hide_labels"],
            hide_conf=vis_params["hide_conf"],
            output_dir=save_dir,
            file_name=filename_wo_ext,
            export_format=vis_params["format"]
        )

        grand_total_predictions += total_prediction_count

    if dataset_json_path:
        save_path = str(save_dir / "result.json")
        save_json(all_coco_preds, save_path)
        
    print(f"\nCompleted {len(image_files)} images.")
    print("Total Prediction Count (Before NMS Merge): ", grand_total_predictions)
    print("Total Prediction Count (After Final NMS Merge): ", len(merged_preds))
    print("Total Prediction time for all images is: {:.2f} ms".format(total_prediction_time * 1000))
    print(f"Prediction results are successfully exported to {save_dir}")


#### **Validation and Test Cases**

#### **1. Single Image**

**YOLOv8-N Model**

In [20]:

# Example usage: Adaptive-Optimized-NMS - 50 epochs mix dataset
# Using Different IoU threshold
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 640

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8__50_detection_model,
    sliced_detection_model = yolov8__50_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 97.33 ms
Total Based pred time: 97.33 ms
Full Image Object Density: 45
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.27 ms
Slice Object Density: 17
********* Slice Parameters ***********
Slice Width:  640
Slice Height:  640
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 2
POST PROCESS:  NMS
Original Prediction Count 53
Final Bounding Box Count (NMS):  14
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 40.04 ms
Pre Adaptive Slicing:  17
Post Adaptive Slicing:  36
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 7.62 ms
Sli

In [22]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> 640 * 640
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp872/result.json' --max_detections 100

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.462
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.851
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.380
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=100 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=100 ] = 0.872
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=100 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.463
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.522
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [15]:
# Example usage: Adaptive-Optimized-NMS - 50 epochs mix dataset
# Using Different IoU threshold
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 640

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=baseline_yolov8_detection_model,
    sliced_detection_model = baseline_yolov8_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************


/mmfs1/cm/shared/apps_local/python/3.11/envs/torch11.8/lib/python3.9/site-packages/torch/nn/modules/conv.py:456: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv2d(input, weight, bias, self.stride,


Base pred time: 767.48 ms
Total Based pred time: 767.48 ms
Full Image Object Density: 5
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.05 ms
Slice Object Density: 2
Prediction time is: 10.05 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 9.45 ms
Slice Object Density: 1
Prediction time is: 9.45 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 9.10 ms
Slice Object Density: 1
Prediction time is: 9.10 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 8.98 ms
Slice Object Density: 1
Prediction time is: 8.98 ms
________________________________________________
Total Prediction Count (Crop+Slice):  10

Completed 1 images.
Total Prediction Count (Before NMS Merge):  10
Total Prediction Count (After Final NMS Merge):  9
Total Prediction time for all images is: 805.06 ms
Prediction results are successfully exported to sliced_predictions/exp870


In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp870/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.00s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [17]:
# Example usage: Adaptive-Optimized-NMS - 50 epochs mix dataset
# Using Different IoU threshold
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8__50_detection_model,
    sliced_detection_model = yolov8__50_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 27.62 ms
Total Based pred time: 27.62 ms
Full Image Object Density: 64
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.96 ms
Slice Object Density: 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 84
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 83.18 ms
Pre Adaptive Slicing:  25
Post Adaptive Slicing:  54
Cropped I

In [18]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp827/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.447
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.870
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.492
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.889
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.690
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.430
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.521
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [13]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 27.17 ms
Total Based pred time: 27.17 ms
Full Image Object Density: 62
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.64 ms
Slice Object Density: 34
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 90
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  7
Sliced Prediction time is: 82.35 ms
Pre Adaptive Slicing:  34
Post Adaptive Slicing:  60
Cropped Image Dimension: 680 0 1360 382
Initi

In [14]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp807/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.471
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.867
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.453
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.854
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.851
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.417
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.521
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [15]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = yolov8_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 28.07 ms
Total Based pred time: 28.07 ms
Full Image Object Density: 62
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.73 ms
Slice Object Density: 27
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 80
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 8

In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp808/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.02s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.480
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.878
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.402
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.908
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.467
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.545
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [17]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov8_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 28.46 ms
Total Based pred time: 28.46 ms
Full Image Object Density: 71
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.72 ms
Slice Object Density: 34
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 90
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  7
Sliced Prediction time is: 82.83 ms
Pre Adaptive Slicing:  34
Post Adaptive Slicing:  60
Cropped Image Dimension: 680 0 1360 382
Initi

In [18]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp809/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.452
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.864
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.399
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.850
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.851
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.417
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.501
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

**YOLOv11-N Model**

In [21]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov11_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 174.11 ms
Total Based pred time: 174.11 ms
Full Image Object Density: 62
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.04 ms
Slice Object Density: 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 74
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 95.15 ms
Pre Adaptive Slicing:  25
Post Adaptive Slicing:  45
Cropped Image Dimension: 680 0 1360 382
In

In [22]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp811/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.440
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.879
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.329
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.909
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.401
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.507
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [32]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = yolov11_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 29.19 ms
Total Based pred time: 29.19 ms
Full Image Object Density: 63
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.15 ms
Slice Object Density: 33
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 84
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 96.88 ms
Pre Adaptive Slicing:  33
Post Adaptive Slicing:  63
Cropped 

In [33]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp816/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.406
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.835
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.243
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.847
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.384
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.475
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [36]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 29.10 ms
Total Based pred time: 29.10 ms
Full Image Object Density: 63
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.90 ms
Slice Object Density: 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 74
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 95.25 ms
Pre Adaptive Slicing:  25
Post Adaptive Slicing:  45
Cropped Image Dimension: 680 0 1360 382
Init

In [37]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp818/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.411
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.838
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.290
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.851
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.401
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.465
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

**Mixed Models**

In [26]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 27.47 ms
Total Based pred time: 27.47 ms
Full Image Object Density: 62
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.48 ms
Slice Object Density: 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 74
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 94.77 ms
Pre Adaptive Slicing:  25
Post Adaptive Slicing:  45
Cropped Image Dimension: 680 0 1360 382
Init

In [27]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp813/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.446
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.896
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.304
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.935
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.401
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.518
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [28]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = yolov11_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 28.22 ms
Total Based pred time: 28.22 ms
Full Image Object Density: 62
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 86.19 ms
Slice Object Density: 33
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 84
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 96.15 ms
Pre Adaptive Slicing:  33
Post Adaptive Slicing:  63
Cropped 

In [29]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp814/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.425
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.842
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.308
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.862
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.384
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.500
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [30]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = yolov8_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 29.48 ms
Total Based pred time: 29.48 ms
Full Image Object Density: 63
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.24 ms
Slice Object Density: 27
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 80
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 8

In [31]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp815/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.452
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.860
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.353
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.889
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.467
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.520
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [38]:
#Using YOLOv8 for full then YOLOv11 for slice predictions (adpative confidence)
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov8_model,
    sliced_detection_model = yolov11_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 29.15 ms
Total Based pred time: 29.15 ms
Full Image Object Density: 71
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 11.27 ms
Slice Object Density: 33
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 84
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 96.65 ms
Pre Adaptive Slicing:  33
Post Adaptive Slicing:  63
Cropped 

In [39]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp819/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.395
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.816
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.244
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.835
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.713
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.384
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.455
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **2. Subset of 50 images**

In [41]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = yolov8_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 30.38 ms
Total Based pred time: 30.38 ms
Full Image Object Density: 68
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.78 ms
Slice Object Density: 18
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 95
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  28
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 87.32 ms
Pre Adaptive Slicing:  18
Post Adaptive Slicing:  76
Cropped Image Dimension: 700 0 1400 394
In

In [43]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp820/result.json'

loading annotations into memory...
Done (t=0.02s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.09s).
Accumulating evaluation results...
DONE (t=0.08s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.184
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.319
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.192
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.233
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.476
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.636
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.123
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.281
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [44]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = yolov11_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 30.95 ms
Total Based pred time: 30.95 ms
Full Image Object Density: 64
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 10.27 ms
Slice Object Density: 18
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 94
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  17
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  6
Sliced Prediction time is: 98.77 ms
Pre Adaptive Slicing:  18
Post Adaptive Slicing:  68
Croppe

In [45]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp821/result.json'

loading annotations into memory...
Done (t=0.05s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.11s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.186
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.315
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.191
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.227
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.473
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.564
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.117
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.289
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [46]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov8_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 31.69 ms
Total Based pred time: 31.69 ms
Full Image Object Density: 84
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.87 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 99
Final Bounding Box Count (NMS):  37
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 86.77 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  77
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.91 ms
S

In [47]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp822/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.97s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.211
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.361
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.221
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.281
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.518
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.577
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.156
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.288
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [48]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov11_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 31.15 ms
Total Based pred time: 31.15 ms
Full Image Object Density: 66
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 10.38 ms
Slice Object Density: 20
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 63
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 96.83 ms
Pre Adaptive Slicing:  20
Post Adaptive Slicing:  51
Cropped Image Dimension: 700 0 1400 394
In

In [49]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp823/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.97s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.198
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.346
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.203
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.260
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.478
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.598
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.139
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.275
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [50]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 29.73 ms
Total Based pred time: 29.73 ms
Full Image Object Density: 68
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 9.58 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 99
Final Bounding Box Count (NMS):  37
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 90.30 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  77
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.95 ms
S

In [51]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp824/result.json'

loading annotations into memory...
Done (t=0.03s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.94s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.215
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.374
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.208
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.290
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.530
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.667
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.157
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.298
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [52]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 32.11 ms
Total Based pred time: 32.11 ms
Full Image Object Density: 64
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 11.34 ms
Slice Object Density: 20
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 63
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 96.22 ms
Pre Adaptive Slicing:  20
Post Adaptive Slicing:  51
Cropped Image Dimension: 700 0 1400 394
In

In [53]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp825/result.json'

loading annotations into memory...
Done (t=0.04s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.94s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.200
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.350
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.196
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.266
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.475
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.602
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.140
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.272
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [15]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8__50_detection_model,
    sliced_detection_model = yolov8__50_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************


/mmfs1/cm/shared/apps_local/python/3.11/envs/torch11.8/lib/python3.9/site-packages/torch/nn/modules/conv.py:456: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv2d(input, weight, bias, self.stride,


Base pred time: 676.67 ms
Total Based pred time: 676.67 ms
Full Image Object Density: 82
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 9.18 ms
Slice Object Density: 24
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 81
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  27
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  8
Sliced Prediction time is: 84.35 ms
Pre Adaptive Slicing:  24
Post Adaptive Slicing:  72
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.68 ms
Slice Object Density: 8
Prediction time is: 7.68 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.75 ms
Slice Object Density: 17
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap 

In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp826/result.json'

loading annotations into memory...
Done (t=0.02s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.02s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.192
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.331
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.253
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.435
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.608
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.135
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.252
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [17]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11__50_detection_model,
    sliced_detection_model = yolov11__50_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 174.04 ms
Total Based pred time: 174.04 ms
Full Image Object Density: 76
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 10.96 ms
Slice Object Density: 21
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 73
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 95.32 ms
Pre Adaptive Slicing:  21
Post Adaptive Slicing:  54
Cropp

In [18]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp830/result.json'

loading annotations into memory...
Done (t=0.16s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.04s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.190
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.331
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.238
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.466
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.638
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.128
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.263
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **3. Mix of 500 images**

**YOLOv8-N model**

In [19]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = yolov8_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 82.40 ms
Total Based pred time: 82.40 ms
Full Image Object Density: 65
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.38 ms
Slice Object Density: 38
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 132
Final Bounding Box Count (NMS):  14
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count

In [21]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp835/result.json'

loading annotations into memory...
Done (t=0.14s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.03s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=18.96s).
Accumulating evaluation results...
DONE (t=0.38s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.152
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.276
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.148
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.195
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.383
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.460
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.091
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.217
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

In [22]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov8_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 84.39 ms
Total Based pred time: 84.39 ms
Full Image Object Density: 75
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 8.64 ms
Slice Object Density: 45
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 129
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count

In [23]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp836/result.json'

loading annotations into memory...
Done (t=0.13s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=16.40s).
Accumulating evaluation results...
DONE (t=0.31s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.168
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.305
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.161
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.222
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.412
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.487
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.106
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.234
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

In [24]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov8_detection_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 25.43 ms
Total Based pred time: 25.43 ms
Full Image Object Density: 65
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.20 ms
Slice Object Density: 45
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 129
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count

In [26]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp837/result.json'

loading annotations into memory...
Done (t=0.13s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=16.09s).
Accumulating evaluation results...
DONE (t=0.44s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.170
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.307
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.164
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.223
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.412
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.498
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.106
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.236
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

**YOLOv11-N model**

In [27]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = yolov11_detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 101.96 ms
Total Based pred time: 101.96 ms
Full Image Object Density: 64
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.99 ms
Slice Object Density: 45
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 156
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  20
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Cou

In [28]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp838/result.json'

loading annotations into memory...
Done (t=0.13s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.03s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=19.17s).
Accumulating evaluation results...
DONE (t=0.38s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.146
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.265
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.142
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.189
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.379
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.424
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.091
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.213
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

In [29]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov11_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 102.69 ms
Total Based pred time: 102.69 ms
Full Image Object Density: 65
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.17 ms
Slice Object Density: 48
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 125
Final Bounding Box Count (NMS):  14
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction tim

In [30]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp839/result.json'

loading annotations into memory...
Done (t=0.18s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=16.68s).
Accumulating evaluation results...
DONE (t=0.30s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.165
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.304
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.157
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.224
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.405
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.490
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.105
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.229
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

In [31]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=yolov11_detection_model,
    sliced_detection_model = mixed_detection_yolov11_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 26.84 ms
Total Based pred time: 26.84 ms
Full Image Object Density: 64
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 10.54 ms
Slice Object Density: 48
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 125
Final Bounding Box Count (NMS):  14
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction time 

In [32]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp840/result.json'

loading annotations into memory...
Done (t=0.14s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=16.52s).
Accumulating evaluation results...
DONE (t=0.30s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.167
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.305
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.161
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.227
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.410
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.456
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.106
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.233
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

#### **4. Subset of 15 images**

In [13]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=mixed_detection_yolov8_model,
    sliced_detection_model = mixed_detection_yolov8_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 15 image(s)...
*****************************************
File Name:  9999963_00000_d_0000057
*****************************************


/mmfs1/cm/shared/apps_local/python/3.11/envs/torch11.8/lib/python3.9/site-packages/torch/nn/modules/conv.py:456: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv2d(input, weight, bias, self.stride,


Base pred time: 627.70 ms
Total Based pred time: 627.70 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.87 ms
Slice Object Density: 2
Prediction time is: 9.87 ms
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 9.19 ms
Slice Object Density: 22
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 12
POST PROCESS:  NMS
Confidence Score:  0.3
Original Prediction Count 61
Final Bounding Box Count (NMS):  21
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 113.70 ms
Pre Adaptive Slicing:  22
Post Adaptive Slicing:  46
Cropped Image Dimension: 0 525 700 1050
Initial Prediction time is: 8.56 ms
Slice Object Density: 4
Prediction time is: 8.56 ms
Cropped Image Dimension: 700 525 1400 1050
Initial Prediction time is: 8.64 ms
Slice Object Density: 3
Prediction time is: 8.64 ms
_____

In [14]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp1076/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.22s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.176
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.308
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.154
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.194
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.396
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.642
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.105
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.209
 Average Precision  (AP) @[ IoU=0.50:0.95 | a